## Uczenie głębokie – przetwarzanie tekstu – laboratoria
# 3. RNN

In [2]:
%pip install --ignore-installed --force-reinstall -v torch torchtext --index-url https://download.pytorch.org/whl/cu118

^C
Note: you may need to restart the kernel to use updated packages.


Using pip 24.0 from c:\Python312\Lib\site-packages\pip (python 3.12)
Looking in indexes: https://download.pytorch.org/whl/cu118
  Using cached https://download.pytorch.org/whl/cu118/torch-2.3.0%2Bcu118-cp312-cp312-win_amd64.whl (2673.0 MB)
  Using cached https://download.pytorch.org/whl/torchtext-0.16.2%2Bcpu-cp312-cp312-win_amd64.whl (1.9 MB)
  Using cached https://download.pytorch.org/whl/filelock-3.13.1-py3-none-any.whl (11 kB)
  Using cached https://download.pytorch.org/whl/typing_extensions-4.9.0-py3-none-any.whl (32 kB)
  Using cached https://download.pytorch.org/whl/sympy-1.12-py3-none-any.whl (5.7 MB)
  Using cached https://download.pytorch.org/whl/networkx-3.2.1-py3-none-any.whl (1.6 MB)
  Using cached https://download.pytorch.org/whl/Jinja2-3.1.3-py3-none-any.whl (133 kB)
  Using cached https://download.pytorch.org/whl/fsspec-2024.2.0-py3-none-any.whl (170 kB)
  Using cached https://download.pytorch.org/whl/mkl-2021.4.0-py2.py3-none-win_amd64.whl (228.5 MB)
  Using cached htt

ERROR: Could not install packages due to an OSError.
Consider using the `--user` option or check the permissions.
Traceback (most recent call last):
  File "c:\Python312\Lib\site-packages\pip\_internal\commands\install.py", line 452, in run
    installed = install_given_reqs(
                ^^^^^^^^^^^^^^^^^^^
  File "c:\Python312\Lib\site-packages\pip\_internal\req\__init__.py", line 72, in install_given_reqs
    requirement.install(
  File "c:\Python312\Lib\site-packages\pip\_internal\req\req_install.py", line 856, in install
    install_wheel(
  File "c:\Python312\Lib\site-packages\pip\_internal\operations\install\wheel.py", line 725, in install_wheel
    _install_wheel(
  File "c:\Python312\Lib\site-packages\pip\_internal\operations\install\wheel.py", line 585, in _install_wheel
    file.save()
  File "c:\Python312\Lib\site-packages\pip\_internal\operations\install\wheel.py", line 378, in save
    os.unlink(self.dest_path)
PermissionError: [WinError 5] Odmowa dostępu: 'c:\\Python3

In [1]:
from collections import Counter
import torch
from torchtext.vocab import vocab
from tqdm import tqdm
from ipywidgets import FloatProgress

import pandas as pd
from nltk.tokenize import word_tokenize
from unidecode import unidecode

AttributeError: partially initialized module 'charset_normalizer' has no attribute 'md__mypyc' (most likely due to a circular import)

In [ ]:
torch.cuda.is_available()

True

In [ ]:
# odczytaj dane treningowe
train = pd.read_csv('train/train.tsv', sep='\t')
train.columns = ["y", "x"]
print("wczytano dane treningowe")
print(train["y"][0], train["x"][0])

# podziel dane treningowe na słowa
# https://www.geeksforgeeks.org/python-word-embedding-using-word2vec/
slowa_train = []
for tekst in train["x"]:
    pom = []
    for slowo in tekst.split(" "):
        #if slowo not in ("<","/s",">","/S","``"):
        pom.append(slowo.lower())
    slowa_train.append(pom)
print("podzielono dane treningowe na słowa")
print(slowa_train[0])

wczytano dane treningowe
O B-PER O O O O O O O O O B-LOC O O O O O O O O O O O B-LOC O O B-PER I-PER O O O O O O O O O O O O O O O O O O O O O O O B-LOC O O O O O O O O O O O O O B-MISC I-MISC I-MISC I-MISC O O O B-PER O O O O O B-LOC O O O O O O O O O O O O O O O O O B-MISC O O B-LOC O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O O B-PER O O O B-PER I-PER O O O O O O O O O O O O O O O O O O O O O O O O B-PER O O O O O O O O B-MISC O O O O O O O O O O O O O O O O O O O O O O O O Rare Hendrix song draft sells for almost $ 17,000 . </S> LONDON 1996-08-22 </S> A rare early handwritten draft of a song by U.S. guitar legend Jimi Hendrix was sold for almost $ 17,000 on Thursday at an auction of some of the late musician 's favourite possessions . </S> A Florida restaurant paid 10,925 pounds ( $ 16,935 ) for the draft of " Ai n't no telling " , which Hendrix penned on a piece of London hotel stationery in late 1966 . </S> At the end of a January 1967 concert in the English ci

In [ ]:
# odczytaj dane testowe dev-0
test_dev0 = pd.read_csv('dev-0/in.tsv', sep='\t')
test_dev0.columns = ["x"]
print("wczytano dane testowe dev-0")
print(test_dev0["x"][0])

# podziel dane testowe na słowa
# https://www.geeksforgeeks.org/python-word-embedding-using-word2vec/
slowa_test_dev0 = []
for tekst in test_dev0["x"]:
    pom = []
    for slowo in tekst.split(" "):
        #if slowo not in ("<","/s",">","/S","``"):
        pom.append(slowo.lower())
    slowa_test_dev0.append(pom)
print("podzielono dane treningowe na słowa")
print(slowa_test_dev0[0])

wczytano dane testowe dev-0
CRICKET - ENGLISH COUNTY CHAMPIONSHIP SCORES . </S> LONDON 1996-08-30 </S> Result and close of play scores in English county championship matches on Friday : </S> Leicester : Leicestershire beat Somerset by an innings and 39 runs . </S> Somerset 83 and 174 ( P. Simmons 4-38 ) , Leicestershire 296 . </S> Leicestershire 22 points , Somerset 4 . </S> Chester-le-Street : Glamorgan 259 and 207 ( A. Dale 69 , H. Morris 69 ; D. Blenkiron 4-43 ) , Durham 114 ( S. Watkin 4-28 ) and 81-3 . </S> Tunbridge Wells : Nottinghamshire 214 ( P. Johnson 84 ; M. McCague 4-55 ) , Kent 108-3 . </S> London ( The Oval ) : Warwickshire 195 , Surrey 429-7 ( C. Lewis 80 not out , M. Butcher 70 , G. Kersey 63 , J. Ratcliffe 63 , D. Bicknell 55 ) . </S> Hove : Sussex 363 ( W. Athey 111 , V. Drakes 52 ; I. Austin 4-37 ) , Lancashire 197-8 ( W. Hegg 54 ) </S> Portsmouth : Middlesex 199 and 426 ( J. Pooley 111 , M. Ramprakash 108 , M. Gatting 83 ) , Hampshire 232 and 109-5 . </S> Chesterfi

In [ ]:
# odczytaj dane testowe A
test_A = pd.read_csv('test-A/in.tsv', sep='\t')
test_A.columns = ["x"]
print("wczytano dane testowe A")
print(test_A["x"][0])

# podziel dane testowe na słowa
# https://www.geeksforgeeks.org/python-word-embedding-using-word2vec/
slowa_test_A = []
for tekst in test_A["x"]:
    pom = []
    for slowo in tekst.split(" "):
        #if slowo not in ("<","/s",">","/S","``"):
        pom.append(slowo.lower())
    slowa_test_A.append(pom)
print("podzielono dane treningowe na słowa")
print(slowa_test_A[0])

wczytano dane testowe A
RUGBY UNION - CUTTITTA BACK FOR ITALY AFTER A YEAR . </S> ROME 1996-12-06 </S> Italy recalled Marcello Cuttitta </S> on Friday for their friendly against Scotland at Murrayfield more than a year after the 30-year-old wing announced he was retiring following differences over selection . </S> Cuttitta , who trainer George Coste said was certain to play on Saturday week , was named in a 21-man squad lacking only two of the team beaten 54-21 by England at Twickenham last month . </S> Stefano Bordon is out through illness and Coste said he had dropped back row Corrado Covi , who had been recalled for the England game after five years out of the national team . </S> Cuttitta announced his retirement after the 1995 World Cup , where he took issue with being dropped from the Italy side that faced England in the pool stages . </S> Coste said he had approached the player two months ago about a comeback . </S> " He ended the World Cup on the wrong note , " Coste said . </S

In [ ]:
def build_vocab(dataset):
    counter = Counter()
    for document in dataset:
        counter.update(document)
    return vocab(counter, specials=["<unk>", "<pad>", "<bos>", "<eos>"])

In [ ]:
v = build_vocab(slowa_train)
v.set_default_index(v["<unk>"])
itos = v.get_itos()  # mapowanie indeksów na tokeny
print(len(itos))  # liczba różnych tokenów w słowniku
print(itos)

20998
['<unk>', '<pad>', '<bos>', '<eos>', 'rare', 'hendrix', 'song', 'draft', 'sells', 'for', 'almost', '$', '17,000', '.', '</s>', 'london', '1996-08-22', 'a', 'early', 'handwritten', 'of', 'by', 'u.s.', 'guitar', 'legend', 'jimi', 'was', 'sold', 'on', 'thursday', 'at', 'an', 'auction', 'some', 'the', 'late', 'musician', "'s", 'favourite', 'possessions', 'florida', 'restaurant', 'paid', '10,925', 'pounds', '(', '16,935', ')', '"', 'ai', "n't", 'no', 'telling', ',', 'which', 'penned', 'piece', 'hotel', 'stationery', 'in', '1966', 'end', 'january', '1967', 'concert', 'english', 'city', 'nottingham', 'he', 'threw', 'sheet', 'paper', 'into', 'audience', 'where', 'it', 'retrieved', 'fan', 'buyers', 'also', 'snapped', 'up', '16', 'other', 'items', 'that', 'were', 'put', 'former', 'girlfriend', 'kathy', 'etchingham', 'who', 'lived', 'with', 'him', 'from', 'to', '1969', 'they', 'included', 'black', 'lacquer', 'and', 'mother', 'pearl', 'inlaid', 'box', 'used', 'store', 'his', 'drugs', 'anonym

In [ ]:
# slownik etykiety - kody etykiet
etykieta_na_kod = {}
licznik = 0
for tekst in train["y"]:
    for etykieta in tekst.split(" "):
        if etykieta not in etykieta_na_kod:
            etykieta_na_kod[etykieta] = licznik
            licznik+=1
print(etykieta_na_kod)

{'O': 0, 'B-PER': 1, 'B-LOC': 2, 'I-PER': 3, 'B-MISC': 4, 'I-MISC': 5, 'I-LOC': 6, 'B-ORG': 7, 'I-ORG': 8}


In [ ]:
# podziel etykiety
kody_etykiet_train = []
for tekst in train["y"]:
    pom = []
    for etykieta in tekst.split(" "):
        pom.append(etykieta_na_kod[etykieta])
    kody_etykiet_train.append(pom)
print(kody_etykiet_train[0])

[0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 1, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 5, 5, 5, 0, 0, 0, 1, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]


In [ ]:
# odczytaj etykiety dev-0
labels_dev0 = pd.read_csv('dev-0/expected.tsv', sep='\t')
labels_dev0.columns = ["y"]
print(labels_dev0["y"][0])

# podziel etykiety
kody_etykiet_dev0 = []
for tekst in labels_dev0["y"]:
    pom = []
    for etykieta in tekst.split(" "):
        pom.append(etykieta_na_kod[etykieta])
    kody_etykiet_dev0.append(pom)
print(kody_etykiet_dev0[0])

O O B-MISC I-MISC I-MISC O O O B-LOC O O O O O O O O O B-MISC O O O O O O O B-LOC O B-ORG O B-ORG O O O O O O O O B-ORG O O O O B-PER I-PER O O O B-ORG O O O B-ORG O O O B-ORG O O O B-LOC O B-ORG O O O O B-PER I-PER O O B-PER I-PER O O B-PER I-PER O O O B-ORG O O B-PER I-PER O O O O O O B-LOC I-LOC O B-ORG O O B-PER I-PER O O B-PER I-PER O O O B-ORG O O O B-LOC O B-LOC I-LOC O O B-ORG O O B-ORG O O B-PER I-PER O O O O B-PER I-PER O O B-PER I-PER O O B-PER I-PER O O B-PER I-PER O O O O B-LOC O B-ORG O O B-PER I-PER O O B-PER I-PER O O B-PER I-PER O O O B-ORG O O B-PER I-PER O O O B-LOC O B-ORG O O O O B-PER I-PER O O B-PER I-PER O O B-PER I-PER O O O B-ORG O O O O O B-LOC O B-ORG O O O O B-ORG O O B-PER I-PER O O B-PER O O O O B-PER I-PER O O B-PER I-PER O O O B-LOC O B-ORG O O O O B-PER I-PER O O O O O B-ORG O O B-PER I-PER O O B-PER I-PER O O O O
[0, 0, 4, 5, 5, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 0, 0, 0, 0, 0, 0, 0, 2, 0, 7, 0, 7, 0, 0, 0, 0, 0, 0, 0, 0, 7, 0, 0, 0, 0, 1, 3, 0

In [ ]:
def data_process(dt):
    # Wektoryzacja dokumentów tekstowych.
    return [
        torch.tensor(
            [v["<bos>"]] + [v[token] for token in document] + [v["<eos>"]],
            dtype=torch.long,
        )
        for document in dt
    ]

def labels_process(dt):
    # Wektoryzacja etykiet (NER)
    return [torch.tensor([0] + document + [0], dtype=torch.long) for document in dt]

In [ ]:
train_tokens_ids = data_process(slowa_train)
test_dev0_tokens_ids = data_process(slowa_test_dev0)
test_A_tokens_ids = data_process(slowa_test_A)

train_labels = labels_process(kody_etykiet_train)
test_dev0_labels = labels_process(kody_etykiet_dev0)

In [ ]:
print(len(train_tokens_ids), len(train_tokens_ids[0]))
print(len(test_dev0_tokens_ids), len(test_dev0_tokens_ids[0]))
print(len(test_A_tokens_ids), len(test_A_tokens_ids[0]))

print(train_tokens_ids[0])
print(test_dev0_tokens_ids[0])
print(test_A_tokens_ids[0])

944 199
214 256
229 283
tensor([  2,   4,   5,   6,   7,   8,   9,  10,  11,  12,  13,  14,  15,  16,
         14,  17,   4,  18,  19,   7,  20,  17,   6,  21,  22,  23,  24,  25,
          5,  26,  27,   9,  10,  11,  12,  28,  29,  30,  31,  32,  20,  33,
         20,  34,  35,  36,  37,  38,  39,  13,  14,  17,  40,  41,  42,  43,
         44,  45,  11,  46,  47,   9,  34,   7,  20,  48,  49,  50,  51,  52,
         48,  53,  54,   5,  55,  28,  17,  56,  20,  15,  57,  58,  59,  35,
         60,  13,  14,  30,  34,  61,  20,  17,  62,  63,  64,  59,  34,  65,
         66,  20,  67,  68,  69,  34,  70,  20,  71,  72,  34,  73,  53,  74,
         75,  26,  76,  21,  17,  77,  13,  14,  78,  79,  80,  81,  82,  83,
         84,  85,  86,  87,  81,   9,  32,  21,   5,  37,  88,  89,  90,  91,
         53,  92,  93,  94,  95,  96,  60,  97,  98,  13,  14,  99, 100,  17,
        101, 102, 103, 104,  20, 105, 106, 107, 108,  21,   5,  97, 109, 110,
        111,  53,  54,  31, 112, 113, 11

In [ ]:
print(len(train_labels), len(train_labels[0]))
print(len(test_dev0_labels), len(test_dev0_labels[0]))

print(train_labels[0])
print(test_dev0_labels[0])

944 199
214 256
tensor([0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        2, 0, 0, 1, 3, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 5, 5, 5, 0, 0,
        0, 1, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 4, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 3, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0,
        0, 0, 0, 0, 0, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0])
tensor([0, 0, 0, 4, 5, 5, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 4, 0, 0, 0, 0,
        0, 0, 0, 2, 0, 7, 0, 7, 0, 0, 0, 0, 0, 0, 0, 0, 7, 0, 0, 0, 0, 1, 3, 0,
        0, 0, 7, 0, 0, 0, 7, 0, 0, 0, 7, 0, 0, 0, 2, 0, 7, 0, 0, 0, 0, 1, 3, 0,
        0, 1, 3, 0, 0, 1, 3, 0, 0, 0, 7, 0, 0, 1, 3, 0, 0, 0, 0, 0, 0, 2, 

In [ ]:
def get_scores(y_true, y_pred):
    # Funkcja zwraca precyzję, pokrycie i F1
    acc_score = 0
    tp = 0
    fp = 0
    selected_items = 0
    relevant_items = 0

    for p, t in zip(y_pred, y_true):
        if p == t:
            acc_score += 1

        if p > 0 and p == t:
            tp += 1

        if p > 0:
            selected_items += 1

        if t > 0:
            relevant_items += 1

    if selected_items == 0:
        precision = 1.0
    else:
        precision = tp / selected_items

    if relevant_items == 0:
        recall = 1.0
    else:
        recall = tp / relevant_items

    if precision + recall == 0.0:
        f1 = 0.0
    else:
        f1 = 2 * precision * recall / (precision + recall)

    return precision, recall, f1

In [ ]:
num_tags = len(etykieta_na_kod.keys())

class LSTM(torch.nn.Module):

    def __init__(self):
        super(LSTM, self).__init__()
        self.emb = torch.nn.Embedding(len(v.get_itos()), 100)
        self.rec = torch.nn.LSTM(100, 256, 1, batch_first=True)
        self.fc1 = torch.nn.Linear(256, num_tags)

    def forward(self, x):
        emb = torch.relu(self.emb(x))
        lstm_output, (h_n, c_n) = self.rec(emb)
        out_weights = self.fc1(lstm_output)
        return out_weights

In [ ]:
def eval_model(dataset_tokens, dataset_labels, model):
    Y_true = []
    Y_pred = []
    for i in tqdm(range(len(dataset_labels))):
        batch_tokens = dataset_tokens[i].unsqueeze(0)
        tags = list(dataset_labels[i].numpy())
        Y_true += tags

        Y_batch_pred_weights = model(batch_tokens).squeeze(0)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights, 1)
        Y_pred += list(Y_batch_pred.numpy())

    return get_scores(Y_true, Y_pred)

In [ ]:
lstm = LSTM()
criterion = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(lstm.parameters())
NUM_EPOCHS = 5

In [ ]:
for i in range(NUM_EPOCHS):
    lstm.train()
    # for i in tqdm(range(500)):
    for i in tqdm(range(len(train_labels))):
        batch_tokens = train_tokens_ids[i].unsqueeze(0)
        tags = train_labels[i].unsqueeze(1)

        predicted_tags = lstm(batch_tokens)

        optimizer.zero_grad()
        loss = criterion(predicted_tags.squeeze(0), tags.squeeze(1))

        loss.backward()
        optimizer.step()

    lstm.eval()

 88%|████████▊ | 832/944 [00:37<00:05, 21.94it/s]


KeyboardInterrupt: 

In [ ]:
print(eval_model(test_dev0_tokens_ids, test_dev0_labels, lstm))

100%|██████████| 214/214 [00:00<00:00, 262.62it/s]


(0.6558005752636625, 0.7225352112676057, 0.687552353828112)
